# SafariHub - Tour Recommender System

## Business Understanding

### Overview
Tourism is a thriving industry in Kenya, and travelers often face the challenge of choosing the right destinations for their trips. Our project aims to address this problem by creating a recommendation system that assists users in discovering personalized tourist destinations in the country.

### Problem Statement

Travelers often struggle to choose the most suitable tourist destinations for their trips. With an overwhelming number of options available, personalized recommendations are crucial. Our project aims to address this challenge by creating a recommendation system that suggests relevant destinations in Kenya based on user preferences and historical interactions.

#### Stakeholders
1. **Travelers**: They seek relevant recommendations based on their preferences, interests, and historical interactions.
2. **Tourism Agencies**: These organizations can enhance user experiences by providing tailored suggestions.
3. **Local Businesses**: Recommendations can drive footfall to local attractions, restaurants, and accommodations.

### Proposed Solution and Metrics of Success
We propose building a hybrid recommendation system that combines collaborative filtering and content-based approaches. Success metrics include accuracy, recall and precision scores.

### Objectives:

- "Build a collaborative filtering model to recommend destinations."
- "Reduce cold-start problem by incorporating content-based features."
- "Model Recall score ≥ 80%"
- "Model Accuracy ≥ 80%"

### Challenges

1. **Data Quality and Diversity**:
   - Presence of missing values, outliers, or inaccuracies.
   - Ensuring diverse and representative data across different types of destinations (e.g., cities, beaches, historical sites) is essential.

2. **Cold-Start Problem**:
   - New users with limited interaction history pose a challenge. How do we recommend destinations for them?
   - Balancing collaborative filtering (based on user behavior) with content-based filtering (based on destination features) is critical.

3. **Scalability and Real-Time Recommendations**:
   - As the user base grows, the system must handle increased computational demands.
   - Providing real-time recommendations during user interactions requires efficient algorithms.

4. **User Engagement and Interpretability**:
   - Recommendations should align with user interests to keep them engaged.
   - Ensuring transparency and interpretability of the recommendation process is important.

### Conclusion
Our project has significant implications for travelers, tourism agencies, and local businesses. By solving this problem, we contribute to enhancing travel experiences and promoting local economies.


In [1]:
# Import modules
import json
import pandas as pd
import numpy as np


In [2]:
# Load the JSON file
with open('data\Tripadvisor1.json', 'r') as file:
    data = json.load(file)

# Now you can access the data as a Python dictionary
data


[{'reviewTags': [{'text': 'meryl streep', 'reviews': 58},
   {'text': 'ngong hills', 'reviews': 104},
   {'text': 'finch hatton', 'reviews': 23},
   {'text': 'coffee plantation', 'reviews': 32},
   {'text': 'guided tour', 'reviews': 67},
   {'text': 'personal guide', 'reviews': 33},
   {'text': 'interesting history', 'reviews': 22},
   {'text': 'worth a visit', 'reviews': 78},
   {'text': 'interesting visit', 'reviews': 25},
   {'text': 'entrance fee', 'reviews': 36},
   {'text': 'gift shop', 'reviews': 37},
   {'text': 'movie', 'reviews': 523},
   {'text': 'africa', 'reviews': 840},
   {'text': 'machinery', 'reviews': 19},
   {'text': 'legacy', 'reviews': 21},
   {'text': 'restored', 'reviews': 19},
   {'text': 'artifacts', 'reviews': 43},
   {'text': 'insight', 'reviews': 37}],
  'category': 'attraction',
  'rating': 4,
  'numberOfReviews': 2281,
  'name': 'Karen Blixen Museum',
  'image': 'https://media-cdn.tripadvisor.com/media/photo-m/1280/16/af/ca/e8/the-karen-blixen-house.jpg',


In [3]:
# Function to extract review tags
def extract_review_tags(review_tags):
    tags = [tag['text'] for tag in review_tags]
    reviews = [tag['reviews'] for tag in review_tags]
    return tags, reviews

# Initialize lists to hold the data
names = []
categories = []
ratings = []
number_of_reviews = []
images = []
photo_counts = []
price_ranges = []
photos_list = []
price_levels = []
review_tags = []
review_counts = []

# Loop through each item in the data
for item in data:
    names.append(item['name'])
    categories.append(item['category'])
    ratings.append(item['rating'])
    number_of_reviews.append(item['numberOfReviews'])
    images.append(item['image'])
    photo_counts.append(item.get('photoCount'))
    price_ranges.append(item.get('priceRange'))
    photos_list.append(item['photos'])
    price_levels.append(item.get('priceLevel'))
    
    tags, reviews = extract_review_tags(item['reviewTags'])
    review_tags.append(tags)
    review_counts.append(reviews)

# Create a DataFrame
df = pd.DataFrame({
    'Name': names,
    'Category': categories,
    'Rating': ratings,
    'NumberOfReviews': number_of_reviews,
    'Image': images,
    'PhotoCount': photo_counts,
    'PriceRange': price_ranges,
    'Photos': photos_list,
    'PriceLevel': price_levels,
    'ReviewTags': review_tags,
    'ReviewCounts': review_counts
})

df.head()

Name    Category  Rating  NumberOfReviews  \
0                   Karen Blixen Museum  attraction     4.0             2281   
1             Hell's Gate National Park  attraction     4.5              949   
2                            Tsavo Park  attraction     4.5             1741   
3     Hilton Garden Inn Nairobi Airport       hotel     4.5              519   
4  PrideInn Flamingo Beach Resort & Spa       hotel     4.5             2922   

                                               Image  PhotoCount   PriceRange  \
0  https://media-cdn.tripadvisor.com/media/photo-...         934         None   
1  https://media-cdn.tripadvisor.com/media/photo-...        1100         None   
2  https://media-cdn.tripadvisor.com/media/photo-...        4466         None   
3  https://media-cdn.tripadvisor.com/media/photo-...         392  $169 - $200   
4  https://media-cdn.tripadvisor.com/media/photo-...        2003  $128 - $218   

                                              Photos PriceLevel  \
0  [https://media-cdn.tripadvisor.com/media/photo...       None   
1  [https://media-cdn.tripadvisor.com/media/photo...       None   
2  [https://media-cdn.tripadvisor.com/media/photo...       None   
3  [https://media-cdn.tripadvisor.com/media/photo...         $$   
4  [https://media-cdn.tripadvisor.com/media/photo...         $$   

                                          ReviewTags  \
0  [meryl streep, ngong hills, finch hatton, coff...   
1  [bike ride, the lion king, wild animals, tomb ...   
2  [national park, great park, red soil, three da...   
3  [close to the airport, nairobi airport, roofto...   
4  [pavilion bar, guest relations, big swimming p...   

                                        ReviewCounts  
0  [58, 104, 23, 32, 67, 33, 22, 78, 25, 36, 37, ...  
1  [40, 21, 43, 11, 9, 11, 20, 7, 7, 43, 16, 7, 1...  
2  [34, 12, 11, 8, 8, 8, 275, 120, 67, 64, 80, 24...  
3  [43, 27, 22, 7, 6, 5, 13, 7, 7, 5, 7, 9, 6, 10...  
4  [25, 110, 27, 81, 52, 43, 30, 27, 25, 23, 22, ...

In [3]:
# Define the list of columns you expect
expected_columns = ["name", "category", "rating", "numberOfReviews", "image", "photoCount", "priceRange", "reviewTags", "photos", "priceLevel"]

# Create a DataFrame while filling missing keys with NaN
df1 = pd.DataFrame([
    {
        col: item.get(col, np.nan) for col in expected_columns
    }
    for item in data
])

# Display the features DataFrame
print("\nFeatures DataFrame:")
df1


Features DataFrame:


name    category  rating  \
0                     Karen Blixen Museum  attraction     4.0   
1               Hell's Gate National Park  attraction     4.5   
2                              Tsavo Park  attraction     4.5   
3       Hilton Garden Inn Nairobi Airport       hotel     4.5   
4    PrideInn Flamingo Beach Resort & Spa       hotel     4.5   
..                                    ...         ...     ...   
586                    iKWETA Safari Camp       hotel     4.5   
587                   GemSuites Riverside       hotel     4.5   
588                       Mara Major Camp       hotel     5.0   
589          Villa Mandhari - Diani Beach       hotel     4.5   
590                    Morning Star Diani       hotel     4.0   

     numberOfReviews                                              image  \
0               2281  https://media-cdn.tripadvisor.com/media/photo-...   
1                949  https://media-cdn.tripadvisor.com/media/photo-...   
2               1741  https://media-cdn.tripadvisor.com/media/photo-...   
3                519  https://media-cdn.tripadvisor.com/media/photo-...   
4               2922  https://media-cdn.tripadvisor.com/media/photo-...   
..               ...                                                ...   
586              383  https://media-cdn.tripadvisor.com/media/photo-...   
587               61  https://media-cdn.tripadvisor.com/media/photo-...   
588               34  https://media-cdn.tripadvisor.com/media/photo-...   
589               41  https://media-cdn.tripadvisor.com/media/photo-...   
590               47  https://media-cdn.tripadvisor.com/media/photo-...   

     photoCount   priceRange  \
0           934          NaN   
1          1100          NaN   
2          4466          NaN   
3           392  $169 - $200   
4          2003  $128 - $218   
..          ...          ...   
586         486  $177 - $206   
587         170  $139 - $301   
588         133  $660 - $760   
589          96  $139 - $234   
590          78    $70 - $88   

                                            reviewTags  \
0    [{'text': 'meryl streep', 'reviews': 58}, {'te...   
1    [{'text': 'bike ride', 'reviews': 40}, {'text'...   
2    [{'text': 'national park', 'reviews': 34}, {'t...   
3    [{'text': 'close to the airport', 'reviews': 4...   
4    [{'text': 'pavilion bar', 'reviews': 25}, {'te...   
..                                                 ...   
586  [{'text': 'affordable luxury', 'reviews': 19},...   
587  [{'text': 'security team', 'reviews': 2}, {'te...   
588  [{'text': 'highly recommend staying here', 're...   
589  [{'text': 'pool', 'reviews': 11}, {'text': 'di...   
590  [{'text': 'a great stay', 'reviews': 2}, {'tex...   

                                                photos priceLevel  
0    [https://media-cdn.tripadvisor.com/media/photo...        NaN  
1    [https://media-cdn.tripadvisor.com/media/photo...        NaN  
2    [https://media-cdn.tripadvisor.com/media/photo...        NaN  
3    [https://media-cdn.tripadvisor.com/media/photo...         $$  
4    [https://media-cdn.tripadvisor.com/media/photo...         $$  
..                                                 ...        ...  
586  [https://media-cdn.tripadvisor.com/media/photo...         $$  
587  [https://media-cdn.tripadvisor.com/media/photo...        $$$  
588  [https://media-cdn.tripadvisor.com/media/photo...       $$$$  
589  [https://media-cdn.tripadvisor.com/media/photo...         $$  
590  [https://media-cdn.tripadvisor.com/media/photo...          $  

[591 rows x 10 columns]

In [4]:

# Load the JSON file
with open('data\Tripadvisor2.json', 'r') as file:
    data2 = json.load(file)

# Now you can access the data as a Python dictionary
data2


[{'photos': ['https://media-cdn.tripadvisor.com/media/photo-o/09/80/6c/4b/saruni-samburu.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/11/de/8e/6d/single-villa-5.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/11/e0/d6/b8/saruni-samburu-suite.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/2c/8b/00/2f/caption.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1d/73/81/b7/panoramic-overview-from.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1d/73/81/b9/panoramic-overview-from.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1d/73/81/ba/the-room.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/23/a3/23/e1/caption.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/23/a3/23/e2/caption.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/23/a3/23/e3/caption.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1c/1d/fd/76/this-is-eric-with-our.jpg'],
  'reviewTags': [{'text': 'outdoor shower', 'reviews': 40

In [5]:
import pandas as pd
import numpy as np

# Define the list of columns you expect
expected_columns = ["name", "category", "rating", "numberOfReviews", "image", "photoCount", "priceRange", "reviewTags", "photos", "priceLevel"]

# Create a DataFrame while filling missing keys with NaN
df2 = pd.DataFrame([
    {
        col: item.get(col, np.nan) for col in expected_columns
    }
    for item in data2
])

# Display the resulting DataFrame
df2.head()


name    category  rating  numberOfReviews  \
0              Saruni Samburu       hotel     5.0              697   
1           Fort Jesus Museum  attraction     4.0              994   
2  Karen Blixen Coffee Garden  attraction     4.5              602   
3               Mara Triangle  attraction     5.0              830   
4               Lake Naivasha  attraction     4.5              438   

                                               image  photoCount  \
0  https://media-cdn.tripadvisor.com/media/photo-...        1178   
1  https://media-cdn.tripadvisor.com/media/photo-...         900   
2  https://media-cdn.tripadvisor.com/media/photo-...         159   
3  https://media-cdn.tripadvisor.com/media/photo-...        1279   
4  https://media-cdn.tripadvisor.com/media/photo-...        1077   

                priceRange                                         reviewTags  \
0  KES 45,419 - KES 97,327  [{'text': 'outdoor shower', 'reviews': 40}, {'...   
1                      NaN  [{'text': 'old town', 'reviews': 132}, {'text'...   
2                      NaN  [{'text': 'movie', 'reviews': 42}, {'text': 'a...   
3                      NaN  [{'text': 'the river', 'reviews': 57}, {'text'...   
4                      NaN  [{'text': 'fish', 'reviews': 31}, {'text': 'bo...   

                                              photos priceLevel  
0  [https://media-cdn.tripadvisor.com/media/photo...       $$$$  
1  [https://media-cdn.tripadvisor.com/media/photo...        NaN  
2  [https://media-cdn.tripadvisor.com/media/photo...        NaN  
3  [https://media-cdn.tripadvisor.com/media/photo...        NaN  
4  [https://media-cdn.tripadvisor.com/media/photo...        NaN

In [6]:
df2.shape

(1000, 10)

In [7]:
# Load the JSON file
with open('data\Tripadvisor3.json', 'r') as file:
    data3 = json.load(file)

# Now you can access the data as a Python dictionary
data3


[{'photos': ['https://media-cdn.tripadvisor.com/media/photo-o/16/9a/88/83/ngutuni-safari-lodge.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/16/9a/8a/48/ngutuni-safari-lodge.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/16/9a/87/53/ngutuni-safari-lodge.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/2c/95/63/e2/caption.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/12/30/66/db/ngutuni-safari-lodge.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/11/d1/d3/51/p-20180107-130718-vhdr.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1c/05/d9/1e/img-20200914-wa0004-largejpg.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1d/31/12/0a/caption.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1d/31/12/0c/caption.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1a/91/5c/23/dscn6626-largejpg.jpg',
   'https://media-cdn.tripadvisor.com/media/photo-o/1a/91/5c/22/dscn6591-largejpg.jpg',
   'https://media-cdn.tr

In [8]:
# Define the list of columns you expect
expected_columns = ["name", "category", "rating", "numberOfReviews", "image", "photoCount", "priceRange", "reviewTags", "photos", "priceLevel"]

# Create a DataFrame while filling missing keys with NaN
df3 = pd.DataFrame([
    {
        col: item.get(col, np.nan) for col in expected_columns
    }
    for item in data3
])

# Display the resulting DataFrame
df3.head()


name    category  rating  numberOfReviews  \
0            Ngutuni Safari Lodge       hotel     4.5              327   
1             Bamburi Beach Hotel       hotel     4.0             1319   
2                     Kozi Suites       hotel     4.0               26   
3                  Kiambethu Farm  attraction     5.0              233   
4  Taita Hills Wildlife Sanctuary  attraction     5.0              105   

                                               image  photoCount  \
0  https://media-cdn.tripadvisor.com/media/photo-...         653   
1  https://media-cdn.tripadvisor.com/media/photo-...        1360   
2  https://media-cdn.tripadvisor.com/media/photo-...          22   
3  https://media-cdn.tripadvisor.com/media/photo-...         291   
4  https://media-cdn.tripadvisor.com/media/photo-...         301   

                  priceRange  \
0    KESÂ 8,046 - KESÂ 9,603   
1  KESÂ 16,481 - KESÂ 22,320   
2    KESÂ 4,672 - KESÂ 7,137   
3                        NaN   
4                        NaN   

                                          reviewTags  \
0  [{'text': 'water hole', 'reviews': 41}, {'text...   
1  [{'text': 'bamburi beach', 'reviews': 138}, {'...   
2  [{'text': 'an early morning flight', 'reviews'...   
3  [{'text': 'indigenous forest', 'reviews': 22},...   
4  [{'text': 'wildlife sanctuary', 'reviews': 3},...   

                                              photos priceLevel  
0  [https://media-cdn.tripadvisor.com/media/photo...          $  
1  [https://media-cdn.tripadvisor.com/media/photo...         $$  
2  [https://media-cdn.tripadvisor.com/media/photo...          $  
3  [https://media-cdn.tripadvisor.com/media/photo...        NaN  
4  [https://media-cdn.tripadvisor.com/media/photo...        NaN

In [9]:
df3.shape

(1499, 10)

In [10]:

dataframes = pd.concat([df1, df2, df3], ignore_index=True)

dataframes.shape

(3090, 10)

In [11]:
# Convert unhashable types (like lists) to strings for duplicate checking
dataframes['reviewTags'] = dataframes['reviewTags'].apply(lambda x: str(x) if isinstance(x, list) else x)
dataframes['photos'] = dataframes['photos'].apply(lambda x: str(x) if isinstance(x, list) else x)

# Check for duplicates
duplicates = dataframes.duplicated()

# Display duplicates
print("Duplicate Rows:")
duplicates.value_counts()

Duplicate Rows:


False    2567
True      523
dtype: int64

In [12]:
# Check for duplicates
duplicates = dataframes.duplicated(keep=False)  # Keep all duplicates

# Display duplicated rows
duplicated_rows = dataframes[duplicates]
print("Duplicated Rows:")
duplicated_rows

Duplicated Rows:


name    category  rating  numberOfReviews  \
0                 Karen Blixen Museum  attraction     4.0             2281   
1           Hell's Gate National Park  attraction     4.5              949   
2                          Tsavo Park  attraction     4.5             1741   
34              Nairobi National Park  attraction     4.5             3562   
35                        Diani Beach  attraction     4.5             1955   
...                               ...         ...     ...              ...   
2645                   Karibuni Lodge       hotel     5.0               35   
2649             Hibiscus Guest House       hotel     4.5               63   
2653                      Camp Ndotto       hotel     5.0               11   
2662  Jumeirah Beach Front Apartments       hotel     4.0               35   
2759           Nkasiri Adventure Park       hotel     4.0               25   

                                                  image  photoCount  \
0     https://media-cdn.tripadvisor.com/media/photo-...         934   
1     https://media-cdn.tripadvisor.com/media/photo-...        1100   
2     https://media-cdn.tripadvisor.com/media/photo-...        4466   
34    https://media-cdn.tripadvisor.com/media/photo-...        4502   
35    https://media-cdn.tripadvisor.com/media/photo-...        1951   
...                                                 ...         ...   
2645  https://media-cdn.tripadvisor.com/media/photo-...          21   
2649  https://media-cdn.tripadvisor.com/media/photo-...          32   
2653  https://media-cdn.tripadvisor.com/media/photo-...          44   
2662  https://media-cdn.tripadvisor.com/media/photo-...          26   
2759  https://media-cdn.tripadvisor.com/media/photo-...          38   

     priceRange                                         reviewTags  \
0           NaN  [{'text': 'meryl streep', 'reviews': 58}, {'te...   
1           NaN  [{'text': 'bike ride', 'reviews': 40}, {'text'...   
2           NaN  [{'text': 'national park', 'reviews': 34}, {'t...   
34          NaN  [{'text': 'city skyline', 'reviews': 60}, {'te...   
35          NaN  [{'text': 'white sand', 'reviews': 108}, {'tex...   
...         ...                                                ...   
2645       None                                                 []   
2649       None                                                 []   
2653       None                                                 []   
2662       None  [{'text': 'view of the ocean', 'reviews': 2}, ...   
2759       None  [{'text': 'team', 'reviews': 4}, {'text': 'act...   

                                                 photos priceLevel  
0     ['https://media-cdn.tripadvisor.com/media/phot...        NaN  
1     ['https://media-cdn.tripadvisor.com/media/phot...        NaN  
2     ['https://media-cdn.tripadvisor.com/media/phot...        NaN  
34    ['https://media-cdn.tripadvisor.com/media/phot...        NaN  
35    ['https://media-cdn.tripadvisor.com/media/phot...        NaN  
...                                                 ...        ...  
2645  ['https://media-cdn.tripadvisor.com/media/phot...       None  
2649  ['https://media-cdn.tripadvisor.com/media/phot...       None  
2653  ['https://media-cdn.tripadvisor.com/media/phot...       None  
2662  ['https://media-cdn.tripadvisor.com/media/phot...       None  
2759  ['https://media-cdn.tripadvisor.com/media/phot...       None  

[920 rows x 10 columns]

In [13]:
karen_blixen_museum_rows = duplicated_rows[duplicated_rows['name'] == 'Karen Blixen Museum']
print("Rows with name 'Karen Blixen Museum':")
karen_blixen_museum_rows


Rows with name 'Karen Blixen Museum':


name    category  rating  numberOfReviews  \
0     Karen Blixen Museum  attraction     4.0             2281   
617   Karen Blixen Museum  attraction     4.0             2281   
1621  Karen Blixen Museum  attraction     4.0             2281   

                                                  image  photoCount  \
0     https://media-cdn.tripadvisor.com/media/photo-...         934   
617   https://media-cdn.tripadvisor.com/media/photo-...         934   
1621  https://media-cdn.tripadvisor.com/media/photo-...         934   

     priceRange                                         reviewTags  \
0           NaN  [{'text': 'meryl streep', 'reviews': 58}, {'te...   
617         NaN  [{'text': 'meryl streep', 'reviews': 58}, {'te...   
1621        NaN  [{'text': 'meryl streep', 'reviews': 58}, {'te...   

                                                 photos priceLevel  
0     ['https://media-cdn.tripadvisor.com/media/phot...        NaN  
617   ['https://media-cdn.tripadvisor.com/media/phot...        NaN  
1621  ['https://media-cdn.tripadvisor.com/media/phot...        NaN

In [14]:
# Check for duplicates and drop them, keeping the first occurrence
dataframes = dataframes.drop_duplicates(keep='first')

# Display the updated DataFrame
print("DataFrame after dropping duplicates:")
dataframes.shape

DataFrame after dropping duplicates:


(2567, 10)

In [16]:
dataframes.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2567 entries, 0 to 3089
Data columns (total 10 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   name             2567 non-null   object 
 1   category         2567 non-null   object 
 2   rating           2564 non-null   float64
 3   numberOfReviews  2567 non-null   int64  
 4   image            2564 non-null   object 
 5   photoCount       2567 non-null   int64  
 6   priceRange       1487 non-null   object 
 7   reviewTags       2567 non-null   object 
 8   photos           2567 non-null   object 
 9   priceLevel       1487 non-null   object 
dtypes: float64(1), int64(2), object(7)
memory usage: 220.6+ KB
